# GRAPH GENERATION

In [6]:
import pandas as pd # To structure and manipulated data in a DataFrame format
import geopandas as gpd # To work with spatial data in a DataFrame
from geopandas import GeoDataFrame # To create a GeoDataFrame from a DataFrame

from shapely.geometry import shape, Point, LineString # To create line geometries that can be used in a GeoDataFrame

import matplotlib.pyplot as plt
plt.rcParams['axes.xmargin'] = 0.1
plt.rcParams['axes.ymargin'] = 0.1
%matplotlib inline


## INPUT DATA

In [7]:
df= pd.read_csv('input/trip_rdp.csv')
df.head()


Unnamed: 0   vehicle  level_1             datetime  speed           y  \
0           0  15C01678        0  2018-04-24 17:56:31    8.0  106.681921   
1          35  15C01678       35  2018-04-24 18:00:12    6.0  106.689102   
2          37  15C01678        0  2018-04-24 18:00:35   12.0  106.689388   
3          44  15C01678        7  2018-04-24 18:01:21   19.0  106.687700   
4          55  15C01678       18  2018-04-24 18:02:59   23.0  106.685060   

           x     heading  vehicleType  time_interval   distance  \
0  10.765486   30.579252          500           11.0  32.364445   
1  10.773236   50.236926          500           12.0  31.346340   
2  10.773686  301.799389          500            8.0  29.614758   
3  10.774692  300.096267          500            7.0  32.880368   
4  10.775964  299.978836          500            5.0  34.104016   

   heading_interval  Trip                        geometry  
0          0.000000     0   POINT (10.7654862 106.681921)  
1         12.138997     0  POINT (10.7732365 106.6891025)  
2        287.721463     2   POINT (10.773686 106.6893876)  
3          0.105420     2      POINT (10.774692 106.6877)  
4          2.363673     2     POINT (10.775964 106.68506)

**Chuyển sang dạng GeoDataframe:**

In [9]:
geometry = [Point(xy) for xy in zip(df.x, df.y)]
# gdf = df.drop(['y', 'x'], axis=1)
# gdf = gdf.sort_values('datetime', ascending = True)
gdf = GeoDataFrame(df, crs="EPSG:4326", geometry=geometry)

gdf['datetime'] = pd.to_datetime(gdf['datetime'])
gdf = gdf.sort_values(['vehicle', 'datetime'], ascending=[True, True])
gdf.reset_index(drop=True, inplace=True)
# show gdf data
gdf.count()

Unnamed: 0          7571
vehicle             7571
level_1             7571
datetime            7571
speed               7571
y                   7571
x                   7571
heading             7571
vehicleType         7571
time_interval       7571
distance            7571
heading_interval    7571
Trip                7571
geometry            7571
dtype: int64

## GRAPH GENERATION ALGORITHM INSTALLATION

According: <a href="https://drive.google.com/file/d/11gg9u5ZpVi4VUvGy1h8-JWzq5UNzqwY6/view?usp=sharing">From GPS Traces to a Routable Road Map (page 8)</a>

## Visualizing data into folium map

In [16]:
import folium
import numpy as np


### helper functions: visualize into folium map

In [13]:

''' get_vehicles() params:
input:
    gdf: geodataframe
output:
    vehicles: list vehicle id
'''
def get_trajecs(gdf):
    # get list trajecs
    trajecs = gdf.drop_duplicates(subset='Trip')['Trip']
    trajecs = np.array(trajecs, dtype=object)
    
    return trajecs

In [14]:
colors = [
    'red',
    'yellow',
    'blue',
    'lightred',
    'orange',
    'green',
    'lightgreen',
    'purple',
    'pink']

def add_point(mapobj, gdf, colors):
    #Nạp x,y từ dataframe vào list coords
    coords = list(zip(gdf["geometry"].x, gdf["geometry"].y))
    #Hiển thị trên mapobj
    for coord in coords:
        folium.CircleMarker(location = coord,
                            radius = 1.5, 
                            fill = True,
                            fill_opacity = 0.75,
                            color = colors,
                            weight = 0.01).add_to(mapobj)
           
def add_lines(mapobj, gdf, color):
    coords = list(zip(gdf["geometry"].x, gdf["geometry"].y))
    folium.PolyLine(coords, color=color, weight=1, opacity=1).add_to(mapobj)
       
    
'''
Hàm hiển thị map.
Tùy chọn:
- mapobj: bản đồ nền
- gdf: geodataframe
- start: lộ trình bắt đầu
- end: lộ trình kết thúc
- mask_type: dạng đường (1) và dạng điểm (0)
'''
def show_n_route(mapobj, gdf, mask_type):
    # Khởi tạo bản đồ mapobj
    f = folium.Figure(height = 600)
    mapobj.add_to(f)

    # Get list trajecs id
    trajecs = get_trajecs(gdf)
    # Show every single trajec
    for idx,id in enumerate(trajecs):
        # get sub trajec
        subgdf = gdf[gdf['Trip'] == id]

        if mask_type == 0:
            add_point(mapobj, subgdf, colors[idx % len(colors)])
        else:
            add_lines(mapobj, subgdf, colors[idx % len(colors)])
  
    return mapobj

### BEFORE APPLYING RDP ALGORITHM

In [19]:
# map
mapobj1 = folium.Map([10.783284, 106.682347], zoom_start = 15, tiles='Cartodb dark_matter')

# show lines fisrt
show_n_route(mapobj1, gdf, 1)
# show points 
show_n_route(mapobj1, gdf, 0)



### AFTER

In [ ]:
# map
mapobj2 = folium.Map([10.783284, 106.682347], zoom_start = 15, tiles='Cartodb dark_matter')

# show lines fisrt
show_n_route(mapobj2, gdf_rdp, 1)
# show points 
show_n_route(mapobj2, gdf_rdp, 0)


Saving output